In [1]:
import pandas as pd
import glob
import numpy as np
from IPython.display import display, HTML
import re
import os
import gc
import requests
import time

In [2]:
pd.set_option('display.max_columns', None)
pd.set_option('display.expand_frame_repr', False)
pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_rows', 500)

In [3]:
column_dtype = {'outpainting': str, 'seed': str, 'version': str, 'quality': str}
df = pd.read_csv('starting_dataset.csv', dtype=column_dtype)

In [4]:
len(df)

16349562

In [5]:
# Filter the data based on the 'Noobs' column
filtered_df = df[df['Noobs'] == False]

# Convert 'Date' column to datetime if it is not already in datetime format
filtered_df['Date'] = pd.to_datetime(filtered_df['Date'])

/tmp/ipykernel_894/2212843517.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtered_df['Date'] = pd.to_datetime(filtered_df['Date'])


In [6]:
len(filtered_df)

15450588

In [7]:
filtered_df.columns

Index(['Date', 'Attachments', 'Reactions', 'channel', 'Contains_Link', 'Noobs',
       'Contains_Open_Quality', 'in_progress', 'variations', 'generation_mode',
       'outpainting', 'upscaled', 'version', 'aspect', 'quality', 'repeat',
       'seed', 'style', 'stylize', 'weird', 'niji', 'username',
       'clean_prompts', 'prompt length'],
      dtype='object')

In [11]:
total_rows_per_user = filtered_df.groupby('username').size().reset_index(name='total_rows')
non_false_upscaled_per_user = filtered_df[filtered_df['upscaled'] != False].groupby('username').size().reset_index(name='non_false_upscaled_count')
merged_df = pd.merge(total_rows_per_user, non_false_upscaled_per_user, on='username', how='left')
merged_df['non_false_upscaled_count'].fillna(0, inplace=True)
top_1000_sorted_df = merged_df.sort_values(by='total_rows', ascending=False).head(1000)

In [8]:
#removing img2img generations
clean_df = filtered_df[filtered_df['Contains_Link'] == False]

In [9]:
#removing noob generations
clean_df = clean_df[clean_df['Noobs'] == False]

In [10]:
# removing not finished images
clean_df = clean_df[clean_df['in_progress'] == False]

In [11]:
# removing variations
clean_df = clean_df[clean_df['variations'] == 'False']

In [12]:
# removing outpainting versions
clean_df = clean_df[clean_df['outpainting'] == 'False']

In [13]:
#keeping only raw
clean_df = clean_df[clean_df['style'] == 'raw']

In [14]:
#getting rid of different weird values
clean_df = clean_df[clean_df['weird'] == 'none']

In [15]:
#getting rid of niji generations
clean_df = clean_df[clean_df['niji'] == False]

In [18]:
len(clean_df_upscaled)

243287

In [17]:
clean_df_upscaled = clean_df[clean_df['upscaled'] != False]

In [19]:
total_rows_per_user = clean_df_upscaled.groupby('username').size().reset_index(name='total_rows')
non_false_upscaled_per_user = clean_df_upscaled[clean_df_upscaled['upscaled'] != False].groupby('username').size().reset_index(name='non_false_upscaled_count')
merged_df = pd.merge(total_rows_per_user, non_false_upscaled_per_user, on='username', how='left')
merged_df['non_false_upscaled_count'].fillna(0, inplace=True)
top_1000_sorted_df = merged_df.sort_values(by='total_rows', ascending=False).head(1000)

In [56]:
top_100 = top_1000_sorted_df[top_1000_sorted_df['non_false_upscaled_count'] >= 50]
unique_usernames = top_100['username'].unique()
filtered_rows_df = clean_df_upscaled[clean_df_upscaled['username'].isin(unique_usernames)]

In [57]:
filtered_rows_df['Date'] = pd.to_datetime(filtered_rows_df['Date'])
filtered_rows_df = filtered_rows_df.sort_values(by='Date')
filtered_rows_df = filtered_rows_df.drop_duplicates(subset='clean_prompts', keep='last')

/tmp/ipykernel_894/1231344319.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtered_rows_df['Date'] = pd.to_datetime(filtered_rows_df['Date'])


In [47]:
username_counts = filtered_rows_df['username'].value_counts()

In [51]:
users_at_least_100 = sum(username_counts >= 100)
users_at_least_250 = sum(username_counts >= 250)
users_at_least_500 = sum(username_counts >= 500)

In [59]:
# Step 1: Create dedicated_folder column
username_counts = filtered_rows_df['username'].value_counts()
filtered_rows_df['dedicated_folder'] = filtered_rows_df['username'].map(lambda x: True if username_counts.get(x, 0) > 100 else False)

In [60]:
filtered_rows_df  = filtered_rows_df[filtered_rows_df['dedicated_folder'] == True]

In [62]:
# Step 2: Create user_rank column
ranked_usernames = username_counts.index.rename("username")
ranked_usernames_df = pd.DataFrame({"username": ranked_usernames, "rank": range(1, len(ranked_usernames) + 1)})
ranked_usernames_df['user_rank'] = "rank_" + ranked_usernames_df['rank'].astype(str)
filtered_rows_df = filtered_rows_df.merge(ranked_usernames_df[['username', 'user_rank']], on='username', how='left')
filtered_rows_df['user_rank'] = filtered_rows_df.apply(lambda x: 'no_rank' if not x['dedicated_folder'] else x['user_rank'], axis=1)

In [63]:
# Step 3: Clean filename function
def clean_filename(filename, max_length=100):
    if not isinstance(filename, str):
        return None
    cleaned_name = re.sub(r'[\\/*?:"<>|]', "", filename)
    return cleaned_name[:max_length]

In [70]:
len(sampled_df)

13613

In [92]:
sampled_df.columns

Index(['Date', 'Attachments', 'Reactions', 'channel', 'Contains_Link', 'Noobs',
       'Contains_Open_Quality', 'in_progress', 'variations', 'generation_mode',
       'outpainting', 'upscaled', 'version', 'aspect', 'quality', 'repeat',
       'seed', 'style', 'stylize', 'weird', 'niji', 'username',
       'clean_prompts', 'prompt length', 'dedicated_folder', 'user_rank'],
      dtype='object')

In [69]:
sampled_df['username'].nunique()

79

In [68]:
sampled_df = (
    filtered_rows_df.groupby('username', group_keys=False)
    .apply(lambda x: x.sample(min(len(x), 250)))
    .reset_index(drop=True)
)

In [71]:
# Import necessary modules
import os
import requests
import time

# Ensure the main dataset folder exists
os.makedirs('clean_raw_dataset', exist_ok=True)

for index, row in sampled_df.iterrows():
    # Your existing logic for saving images and texts
    image_url = row['Attachments']
    prompt = row['clean_prompts']
    file_name = clean_filename(prompt)
    
    if file_name is None:
        print(f"Skipping row {index}: invalid or missing prompt")
        continue

    # Get the file extension from the image URL
    file_extension = os.path.splitext(image_url)[1]

    # Determine the folder name based on the dedicated_folder value
    folder_name = row['user_rank'] if row['dedicated_folder'] else 'other'

    # Create the folder within 'clean_mj_dataset' if it does not exist
    full_folder_path = os.path.join('clean_raw_dataset', folder_name)
    os.makedirs(full_folder_path, exist_ok=True)

    # Combine the folder name, file name, and extension to form the image and text file paths
    image_file_path = os.path.join(full_folder_path, file_name + file_extension)
    text_file_path = os.path.join(full_folder_path, file_name + '.txt')

    # Download and save the image
    max_retries = 3
    for attempt in range(max_retries):
        try:
            response = requests.get(image_url)
            with open(image_file_path, 'wb') as f:
                f.write(response.content)
            break
        except requests.exceptions.RequestException as e:
            if attempt < max_retries - 1:
                print(f"Error downloading image at row {index} (attempt {attempt + 1}): {str(e)}")
                time.sleep(5)  # Wait for 5 seconds before retrying
            else:
                print(f"Failed to download image at row {index} after {max_retries} attempts: {str(e)}")
                continue

    # Create and save the text file using the full original prompt as the content
    with open(text_file_path, 'w', encoding='utf-8') as f:
        f.write(prompt)

In [100]:
total_txt_files = sum([len([file for file in files if file.endswith('.txt')]) for subdir, dirs, files in os.walk('clean_mj_dataset')])


In [101]:
total_txt_files

20715

In [56]:
clean_df['niji'].value_counts()

niji
False    10181359
True       307165
Name: count, dtype: int64

In [15]:
sorted_df = merged_df.sort_values(by='total_rows', ascending=False).head(1000)
sorted_df.to_csv('top_1000_users.csv', index=False)

In [16]:
niji_filtered_df = filtered_df[filtered_df['niji'] == True]
len(niji_filtered_df)

631034

In [22]:
niji_total_rows_per_user = niji_filtered_df.groupby('username').size().reset_index(name='total_rows')
niji_non_false_upscaled_per_user = niji_filtered_df[niji_filtered_df['upscaled'] != False].groupby('username').size().reset_index(name='niji_non_false_upscaled_per_user')
niji_merged_df = pd.merge(niji_total_rows_per_user, niji_non_false_upscaled_per_user, on='username', how='left')
niji_merged_df['niji_non_false_upscaled_per_user'].fillna(0, inplace=True)
niji_top_1000_sorted_df = niji_merged_df.sort_values(by='total_rows', ascending=False).head(1000)

In [37]:
niji_top_1000_sorted_df.columns

Index(['username', 'total_rows', 'niji_non_false_upscaled_per_user'], dtype='object')

In [39]:
niji_top_100 = niji_top_1000_sorted_df[niji_top_1000_sorted_df['niji_non_false_upscaled_per_user'] >= 100]

In [35]:
niji_upscaled_filtered_df = niji_filtered_df[niji_filtered_df['upscaled'] != False]
len(niji_upscaled_filtered_df)

252476

In [40]:
unique_usernames = niji_top_100['username'].unique()
filtered_rows_df = niji_upscaled_filtered_df[niji_upscaled_filtered_df['username'].isin(unique_usernames)]

In [45]:
len(filtered_rows_df)

34997

In [47]:
# Step 1: Create dedicated_folder column
username_counts = filtered_rows_df['username'].value_counts()
filtered_rows_df['dedicated_folder'] = filtered_rows_df['username'].map(lambda x: True if username_counts.get(x, 0) > 100 else False)

In [49]:
# Step 2: Create user_rank column
ranked_usernames = username_counts.index.rename("username")
ranked_usernames_df = pd.DataFrame({"username": ranked_usernames, "rank": range(1, len(ranked_usernames) + 1)})
ranked_usernames_df['user_rank'] = "rank_" + ranked_usernames_df['rank'].astype(str)
filtered_rows_df = filtered_rows_df.merge(ranked_usernames_df[['username', 'user_rank']], on='username', how='left')
filtered_rows_df['user_rank'] = filtered_rows_df.apply(lambda x: 'no_rank' if not x['dedicated_folder'] else x['user_rank'], axis=1)

In [51]:
# Step 3: Clean filename function
def clean_filename(filename, max_length=100):
    if not isinstance(filename, str):
        return None
    cleaned_name = re.sub(r'[\\/*?:"<>|]', "", filename)
    return cleaned_name[:max_length]

In [54]:
# Step 4: Loop through DataFrame rows
os.makedirs('niji_dataset', exist_ok=True)

for index, row in filtered_rows_df.iterrows():
    # Your existing logic for saving images and texts
    image_url = row['Attachments']
    prompt = row['clean_prompts']
    file_name = clean_filename(prompt)
    
    if file_name is None:
        print(f"Skipping row {index}: invalid or missing prompt")
        continue

    # Get the file extension from the image URL
    file_extension = os.path.splitext(image_url)[1]

    # Determine the folder name based on the dedicated_folder value
    folder_name = row['user_rank'] if row['dedicated_folder'] else 'other'

    # Create the folder within 'images_v_5.1' if it does not exist
    full_folder_path = os.path.join('images_v_5.1', folder_name)
    os.makedirs(full_folder_path, exist_ok=True)

    # Combine the folder name, file name, and extension to form the image and text file paths
    image_file_path = os.path.join(full_folder_path, file_name + file_extension)
    text_file_path = os.path.join(full_folder_path, file_name + '.txt')

    # Download and save the image
    max_retries = 3
    for attempt in range(max_retries):
        try:
            response = requests.get(image_url)
            with open(image_file_path, 'wb') as f:
                f.write(response.content)
            break
        except requests.exceptions.RequestException as e:
            if attempt < max_retries - 1:
                print(f"Error downloading image at row {index} (attempt {attempt + 1}): {str(e)}")
                time.sleep(5)  # Wait for 5 seconds before retrying
            else:
                print(f"Failed to download image at row {index} after {max_retries} attempts: {str(e)}")
                continue

    # Create and save the text file using the full original prompt as the content
    with open(text_file_path, 'w', encoding='utf-8') as f:
        f.write(prompt)

Skipping row 33560: invalid or missing prompt


In [50]:
filtered_rows_df

Date                                                                                                                                                                             Attachments Reactions     channel  Contains_Link  Noobs  Contains_Open_Quality  in_progress variations generation_mode outpainting  upscaled version aspect quality  repeat   seed       style stylize weird  niji     username                                                                                                                                                                                                                                                                                 clean_prompts  prompt length  dedicated_folder user_rank
0     2023-04-20 00:04:00  https://cdn.discordapp.com/attachments/995431305066065950/1098278001222897726/Tim_Collins_Pennywise_as_a_kids_cartoon_main_character_Simpsons_4db7baee-3382-4d72-bb6b-200ca6c2d720.png       NaN  general-19          False  False                  False        False      False           False       False      True     NaN    1:1       1       0  False        none     250  none  True          Tim                                                                                                                                                                                                                                         Pennywise as a kids cartoon main character, Simpsons              53             False   no_rank
1     2023-04-20 00:07:00  https://cdn.discordapp.com/attachments/989274728155992124/1098278805417754664/Nikki_Crescent_young_beautiful_woman_slavic_Caucasian_on_a_date_29ebe2ef-c39c-464b-9ee6-e8444a896c39.png       NaN   general-8          False  False                  False        False      False           False       False      True     NaN    4:5       1       0  False        none       1  none  True        Nikki                                                                                                                 young beautiful woman, slavic Caucasian, on a date, hugebust chest, insanely realistic full body photo of a stunning woman, Maxim, flirty, hyperreal, painting by Ross Tran,             173              True   rank_65
2     2023-04-20 00:12:00  https://cdn.discordapp.com/attachments/989274728155992124/1098280076640014437/Nikki_Crescent_amazing_beautiful_geisha_insanely_realistic_full_895baaf6-0e18-49e2-a7c3-028e0493321e.png       NaN   general-8          False  False                  False        False      False           False       False      True       5   9:16       1       0  False        none       1  none  True        Nikki  amazing beautiful geisha, insanely realistic full  body photo of a standing geisha by Maxim, very tempting flirty womens luxury underclothes, hyperreal, bedroom background, huge juicy largebust chest, realistically proportioned, impressionist painting by Ross Tran and Helmuth Newton             284              True   rank_65
3     2023-04-20 00:15:00  https://cdn.discordapp.com/attachments/989274728155992124/1098280674047311993/Nikki_Crescent_young_beautiful_woman_slavic_Caucasian_performin_d5d22ebc-e506-41c3-86d3-8080c686c43e.png       NaN   general-8          False  False                  False        False      False           False       False      True     NaN    4:5       1       0  False        none       1  none  True        Nikki                                                                                            young beautiful woman, slavic Caucasian, performing on a webcam, largebust chest, juicy, insanely realistic full body photo of a stunning woman, Maxim, flirty, hyperreal, painting by Ross Tran,             194              True   rank_65
4     2023-04-20 00:22:00  https://cdn.discordapp.com/attachments/989274728155992124/1098282391610597396/Nikki_Crescent_young_beautiful_woman_flirting_lip_bite_slavic_C_37849a3d-6039-4426-af15-a11357cd8fac.png       NaN   general-8          False  False             

In [99]:
import os
import shutil

source_dir = "./clean_raw_dataset/"
destination_dir = "raw_combined"  # A relative path which should be in your current working directory

if not os.path.exists(destination_dir):
    os.makedirs(destination_dir, exist_ok=True)

for foldername, subfolders, filenames in os.walk(source_dir):
    for filename in filenames:
        file_path = os.path.join(foldername, filename)
        destination_path = os.path.join(destination_dir, filename)
        
        # Ensure the destination file doesn't already exist.
        if not os.path.exists(destination_path):
            print(f"Copying {file_path} to {destination_path}")
            shutil.copy(file_path, destination_path)
        else:
            print(f"Skipping {file_path}, as it exists in the destination.")


Copying ./clean_raw_dataset/rank_64/closeup shot of a beautiful stunning kpop girl, flirty latex casual clothes, gorgeous body features,.txt to raw_combined/closeup shot of a beautiful stunning kpop girl, flirty latex casual clothes, gorgeous body features,.txt
Copying ./clean_raw_dataset/rank_64/movie storyboard drawing, a femmefatal woman standing by a car, ink line drawing, monochrome .txt to raw_combined/movie storyboard drawing, a femmefatal woman standing by a car, ink line drawing, monochrome .txt
Copying ./clean_raw_dataset/rank_64/lady in elegant nightie in a luxury hotel room, Japanese top model, short black hair, beautiful, att.png to raw_combined/lady in elegant nightie in a luxury hotel room, Japanese top model, short black hair, beautiful, att.png
Copying ./clean_raw_dataset/rank_64/Closeup, Enigmatic, Allwhite Mongolian Princess, beautiful, mystic, highly detailed, posterlike, whi.txt to raw_combined/Closeup, Enigmatic, Allwhite Mongolian Princess, beautiful, mystic, hig

Copying ./clean_raw_dataset/rank_16/Visualize a scene that encapsulates the essence of experiencing the convenience and quality of Handy.txt to raw_combined/Visualize a scene that encapsulates the essence of experiencing the convenience and quality of Handy.txt
Copying ./clean_raw_dataset/rank_16/Visualize a dynamic and hightech scene that embodies the essence of Bluetti Power Stations. The sett.txt to raw_combined/Visualize a dynamic and hightech scene that embodies the essence of Bluetti Power Stations. The sett.txt
Copying ./clean_raw_dataset/rank_16/Create a hyperrealistic image that captures the essence of uMobix, the ultimate parental control sof.png to raw_combined/Create a hyperrealistic image that captures the essence of uMobix, the ultimate parental control sof.png
Copying ./clean_raw_dataset/rank_16/A vibrant and bustling scene from the heart of a city, captured in the style of a highdefinition tra.txt to raw_combined/A vibrant and bustling scene from the heart of a city, ca

Copying ./clean_raw_dataset/rank_26/Picture an ultradetailed closeup portrait of a modern supermodel, where each striking feature is acc.png to raw_combined/Picture an ultradetailed closeup portrait of a modern supermodel, where each striking feature is acc.png
Copying ./clean_raw_dataset/rank_26/Geometric Symmetry AI Mastery, Artistic Revolution, Insight, hyperdetailed .png to raw_combined/Geometric Symmetry AI Mastery, Artistic Revolution, Insight, hyperdetailed .png
Copying ./clean_raw_dataset/rank_4/a high mountain rising above the sea in the pacific ocean, similar to the Faroe Islands. The mountai.txt to raw_combined/a high mountain rising above the sea in the pacific ocean, similar to the Faroe Islands. The mountai.txt
Copying ./clean_raw_dataset/rank_4/a portrait of a candid female violinist on the top of the hill in a grass meadow inspired by Klimt, .txt to raw_combined/a portrait of a candid female violinist on the top of the hill in a grass meadow inspired by Klimt, .txt
Copy

Copying ./clean_raw_dataset/rank_2/stock photo of a cup hot matcha, food photography, advertising photography, intricate details, hyper.txt to raw_combined/stock photo of a cup hot matcha, food photography, advertising photography, intricate details, hyper.txt
Copying ./clean_raw_dataset/rank_2/stock photo of macarons in the kitchen table, assorted colors, shapes and sizes, without text .txt to raw_combined/stock photo of macarons in the kitchen table, assorted colors, shapes and sizes, without text .txt
Copying ./clean_raw_dataset/rank_2/stock photo of professional food photography, ice cubes, light background, advertising photography, .txt to raw_combined/stock photo of professional food photography, ice cubes, light background, advertising photography, .txt
Copying ./clean_raw_dataset/rank_2/stock photo of jelly, food photography, isolated white background .png to raw_combined/stock photo of jelly, food photography, isolated white background .png
Copying ./clean_raw_dataset/rank_2/C

Copying ./clean_raw_dataset/rank_15/Dosas Thin and crispy fermented rice and lentil crepes served with coconut chutney and sambar. kitch.txt to raw_combined/Dosas Thin and crispy fermented rice and lentil crepes served with coconut chutney and sambar. kitch.txt
Copying ./clean_raw_dataset/rank_15/Sashimi Fresh, thinly sliced raw fish or seafood served with soy sauce and wasabi. kitchen. Captured.txt to raw_combined/Sashimi Fresh, thinly sliced raw fish or seafood served with soy sauce and wasabi. kitchen. Captured.txt
Copying ./clean_raw_dataset/rank_15/stock photo of water splash, with Sweet potatoes Isometric food, isolated on white background, witho.png to raw_combined/stock photo of water splash, with Sweet potatoes Isometric food, isolated on white background, witho.png
Copying ./clean_raw_dataset/rank_15/Okonomiyaki A Hiroshimastyle variation of okonomiyaki that features layers of cabbage, noodles, and .txt to raw_combined/Okonomiyaki A Hiroshimastyle variation of okonomiyaki tha

...

Copying ./clean_raw_dataset/rank_19/Fishhook cactus .txt to raw_combined/Fishhook cactus .txt
Copying ./clean_raw_dataset/rank_19/monkey in onsen, winter, heavy snow .txt to raw_combined/monkey in onsen, winter, heavy snow .txt
Copying ./clean_raw_dataset/rank_19/hay bale in field isolated .txt to raw_combined/hay bale in field isolated .txt
Copying ./clean_raw_dataset/rank_19/turtle eating plastic .png to raw_combined/turtle eating plastic .png
Copying ./clean_raw_dataset/rank_19/flying dog .png to raw_combined/flying dog .png
Copying ./clean_raw_dataset/rank_19/isolated of palm tree on white background, realistic, no shadow .txt to raw_combined/isolated of palm tree on white background, realistic, no shadow .txt
Copying ./clean_raw_dataset/rank_19/A bull with vibrant, anthropomorphic features, adorned with colorful ribbons and accessories, posing.png to raw_combined/A bull with vibrant, anthropomorphic features, adorned with colorful ribbons and accessories, posing.png
Copying ./clea

Copying ./clean_raw_dataset/rank_21/Huge tiger alphamale, roaring, side view, dynamic scene, wide angle, hyperrealistic, photorealistic,.png to raw_combined/Huge tiger alphamale, roaring, side view, dynamic scene, wide angle, hyperrealistic, photorealistic,.png
Copying ./clean_raw_dataset/rank_21/Puma in a chase, side view, dynamic scene, hyperrealistic, photorealistic, high details, high qualit.txt to raw_combined/Puma in a chase, side view, dynamic scene, hyperrealistic, photorealistic, high details, high qualit.txt
Copying ./clean_raw_dataset/rank_21/Cyborg with Bob Dylans face .txt to raw_combined/Cyborg with Bob Dylans face .txt
Copying ./clean_raw_dataset/rank_21/Reindeers herd running, side view, dynamic scene, hyperrealistic, photorealistic, high details, high.png to raw_combined/Reindeers herd running, side view, dynamic scene, hyperrealistic, photorealistic, high details, high.png
Copying ./clean_raw_dataset/rank_21/Beautiful giant angel floating in the air, high above a dest

Copying ./clean_raw_dataset/rank_29/Detailed realistic portrait of retrofuturistic robot in a vibrant coastal environment wearing a worn.txt to raw_combined/Detailed realistic portrait of retrofuturistic robot in a vibrant coastal environment wearing a worn.txt
Copying ./clean_raw_dataset/rank_29/snow leopard, photo by Canon 5D Mark IV with a Canon 85mm f1.2 lens, ISO 300, Aperture f2.5, Shutter.png to raw_combined/snow leopard, photo by Canon 5D Mark IV with a Canon 85mm f1.2 lens, ISO 300, Aperture f2.5, Shutter.png
Copying ./clean_raw_dataset/rank_29/black sphynxcat, pain and suffering, uffering, art, arthouse psychedelic poster 1932, in the style o.png to raw_combined/black sphynxcat, pain and suffering, uffering, art, arthouse psychedelic poster 1932, in the style o.png
Copying ./clean_raw_dataset/rank_29/45yo woman in miniskirt and stockings barefoot, ankle tattoo, stylishly unbuttoned shirt, perfect ma.png to raw_combined/45yo woman in miniskirt and stockings barefoot, ankle tat

Copying ./clean_raw_dataset/rank_8/an image of a beautiful northern European lady standing in a silver jacket in front of a wall with m.png to raw_combined/an image of a beautiful northern European lady standing in a silver jacket in front of a wall with m.png
Copying ./clean_raw_dataset/rank_8/Professional Photography, street Photography of an Aztec tlatoani called Andres Manuel Lopez Obrador.txt to raw_combined/Professional Photography, street Photography of an Aztec tlatoani called Andres Manuel Lopez Obrador.txt
Copying ./clean_raw_dataset/rank_8/Full shot Advertising Photo shoot of a beautiful northern European red hair dressed in silver wearin.png to raw_combined/Full shot Advertising Photo shoot of a beautiful northern European red hair dressed in silver wearin.png
Copying ./clean_raw_dataset/rank_8/two disney princesses in the water looking outward, in the style of light emerald and dark crimson, .png to raw_combined/two disney princesses in the water looking outward, in the st

Copying ./clean_raw_dataset/rank_51/A grey wolf with pitiless eyes tattoo style trash polka. Drawing on paper .txt to raw_combined/A grey wolf with pitiless eyes tattoo style trash polka. Drawing on paper .txt
Copying ./clean_raw_dataset/rank_51/silhouetted female armed calavera tattoo style. Drawing on white paper .png to raw_combined/silhouetted female armed calavera tattoo style. Drawing on white paper .png
Copying ./clean_raw_dataset/rank_51/Dragon tattoo by Sailor Jerry. Drawing on paper .txt to raw_combined/Dragon tattoo by Sailor Jerry. Drawing on paper .txt
Copying ./clean_raw_dataset/rank_51/deaths head sphinx and poppies black yakuza tattoo style. Drawing on white paper .png to raw_combined/deaths head sphinx and poppies black yakuza tattoo style. Drawing on white paper .png
Copying ./clean_raw_dataset/rank_51/high key portrait of the fashion woman, halflength portrait, by Robby Cavanaugh .png to raw_combined/high key portrait of the fashion woman, halflength portrait, by Rob

In [100]:
import os

# Specify the directory to check
directory_path = "raw_combined"

# Get all files in the directory
all_files = [f for f in os.listdir(directory_path) if os.path.isfile(os.path.join(directory_path, f))]

# Categorize files into image files and text files
image_files = [f for f in all_files if f.endswith(('.png', '.jpg', '.jpeg', '.bmp', '.tiff'))]
text_files = [f for f in all_files if f.endswith('.txt')]

# Extract base names (without extensions) for easy comparison
image_basenames = set(os.path.splitext(f)[0] for f in image_files)
text_basenames = set(os.path.splitext(f)[0] for f in text_files)

# Determine paired files
paired_files = image_basenames.intersection(text_basenames)

# Check for images without corresponding text files
images_without_texts = image_basenames - text_basenames
for img_base in images_without_texts:
    print(f"Image without corresponding text file: {img_base}.[image_extension]")

# Check for text files without corresponding images
texts_without_images = text_basenames - image_basenames
for txt_base in texts_without_images:
    print(f"Text file without corresponding image: {txt_base}.txt")

# Print the count of paired files
print(f"\nTotal number of paired files: {len(paired_files)}")


Total number of paired files: 11481


In [101]:
import os
import shutil
import random
import hashlib

# Specify the directory containing the data and directories for training and validation datasets
source_directory = "raw_combined"
training_directory = "training_data"
validation_directory = "validation_data"

# Ratio for the split. For example, 0.8 means 80% for training and 20% for validation
split_ratio = 0.85

# Extract base names (pairs) from earlier code
paired_files_list = list(image_basenames.intersection(text_basenames))

# Shuffle and split the paired base filenames
random.shuffle(paired_files_list)
split_index = int(len(paired_files_list) * split_ratio)
training_pairs = paired_files_list[:split_index]
validation_pairs = paired_files_list[split_index:]

# Create training and validation directories if they don't exist
os.makedirs(training_directory, exist_ok=True)
os.makedirs(validation_directory, exist_ok=True)

def generate_hashed_name(base_name, extension):
    """Generate a hashed filename using the original base_name."""
    hash_name = hashlib.md5(base_name.encode()).hexdigest()
    return f"{hash_name}.{extension}"

# Helper function to move paired files
def move_paired_files(pairs, target_directory):
    for base_name in pairs:
        # Strip whitespaces and match based on exact base name and extension
        img_file = next(f for f in image_files if os.path.splitext(f)[0].strip() == base_name.strip())
        txt_file = next(f for f in text_files if os.path.splitext(f)[0].strip() == base_name.strip())
        
        # Construct absolute paths
        source_img_path = os.path.abspath(os.path.join(source_directory, img_file))
        source_txt_path = os.path.abspath(os.path.join(source_directory, txt_file))
        target_img_path = os.path.abspath(os.path.join(target_directory, generate_hashed_name(base_name, "png")))
        target_txt_path = os.path.abspath(os.path.join(target_directory, generate_hashed_name(base_name, "txt")))
        
        # Check if the files exist before moving
        if not os.path.exists(source_img_path):
            print(f"Image file not found: {source_img_path}")
            continue
        if not os.path.exists(source_txt_path):
            print(f"Text file not found: {source_txt_path}")
            continue
        
        # Move the files
        shutil.move(source_img_path, target_img_path)
        shutil.move(source_txt_path, target_txt_path)


# Move files to training and validation directories
move_paired_files(training_pairs, training_directory)
move_paired_files(validation_pairs, validation_directory)

print(f"Moved {len(training_pairs)} pairs to {training_directory}")
print(f"Moved {len(validation_pairs)} pairs to {validation_directory}")

Image file not found: /home/irakli/FoxJourney/raw_combined/Fresh baked pizza closeup, traditional wood fired oven background .png
Image file not found: /home/irakli/FoxJourney/raw_combined/hyperrealistic photography extreme closeup of one heron, heron colors, loving look.png
Image file not found: /home/irakli/FoxJourney/raw_combined/image of heart beating , Digital collage, .png
Image file not found: /home/irakli/FoxJourney/raw_combined/lightning thunder strike, centered in image on black background .png
Image file not found: /home/irakli/FoxJourney/raw_combined/a sketchy colorful hand drawn portrait of a beautiful dragon, orange and black, yin and yang.png
Image file not found: /home/irakli/FoxJourney/raw_combined/Gothic Infinity Gauntlet directed by Tim Burton .png
Moved 9758 pairs to training_data
Moved 1723 pairs to validation_data


In [98]:
problematic_file = 'Gothic Infinity Gauntlet directed by Tim Burton '
matching_files = [f for f in all_files if problematic_file in f]
print(matching_files)

['Gothic Infinity Gauntlet directed by Tim Burton .txt', 'Gothic Infinity Gauntlet directed by Tim Burton .png']
